In [ ]:
import ibis
from ibis import _
import streamlit as st
import ibis.expr.datatypes as dt  # Make sure to import the necessary module


conn = ibis.duckdb.connect(extensions=["spatial"])

state_boundaries = "https://data.source.coop/cboettig/us-boundaries/us-state-territory.parquet"
county_boundaries = "https://data.source.coop/cboettig/us-boundaries/us-county.parquet"
states = conn.read_parquet(state_boundaries).rename(state_id = "STUSPS", state = "NAME")
county = conn.read_parquet(county_boundaries).rename(county = "NAMELSAD", state = "STATE_NAME")

localities_boundaries = "us_localities.parquet"
locality = conn.read_parquet(localities_boundaries)


votes = conn.read_csv("landvote.csv")

In [ ]:
vote_states = (votes
                .filter(_["Jurisdiction Type"] == "State")
                .rename(state_id = "State")
                .rename(amount = 'Conservation Funds at Stake', yes = '% Yes')
                .mutate(amount_n=_.amount.replace('$', '').replace(',', '').cast('float'))
                .mutate(log_amount=_.amount_n.log())
                .mutate(year=_['Date'].year().cast('int32'))
                .mutate(
                    yes=ibis.case()
                        .when(_.yes.isin(['Pass', 'None','Fail']), None)  # Handle non-numeric cases
                        .when(_.yes.notnull(), (_.yes.replace('%', '').cast('float').round(2).cast(dt.float64)).cast(dt.string) + '%')  # Convert valid percentages and add %
                        .else_(None)  # Default to None for other cases
                        .end()
                )
               .mutate(log_amount = _.log_amount.round(4))
               .select('state_id', 'Status', 'yes', 'year', 'amount', 'log_amount', )
               )

df_states = (states
            .select('state_id','geometry')
            .right_join(vote_states, "state_id")
            .mutate(key = _.state_id)
            .select('key','geometry','Status', 'yes', 'year', 'amount', 'log_amount')
            .mutate(jurisdiction = ibis.literal("State"))
            .cast({"geometry": "geometry"})
             )


In [ ]:
vote_county = (votes
                .filter(_["Jurisdiction Type"] == "County")
                .rename(county = "Jurisdiction Name", state_id = "State")
                .mutate(key = _.county + ibis.literal('-') + _.state_id)
                .rename(amount = 'Conservation Funds at Stake', yes = '% Yes')
                .mutate(amount_n=_.amount.replace('$', '').replace(',', '').cast('float'))
                .mutate(log_amount=_.amount_n.log())
                .mutate(year=_['Date'].year().cast('int32'))
                .mutate(
                    yes=ibis.case()
                        .when(_.yes.isin(['Pass', 'None','Fail']), None)  # Handle non-numeric cases
                        .when(_.yes.notnull(), (_.yes.replace('%', '').cast('float').round(2).cast(dt.float64)).cast(dt.string) + '%')  # Convert valid percentages and add %
                        .else_(None)  # Default to None for other cases
                        .end()
                )
               .mutate(log_amount = _.log_amount.round(4))
                .select('key', 'Status', 'yes', 'year', 'amount', 'log_amount', )
               )
df_county = (county
            .join(states.select("state", "state_id"), "state")
            .mutate(key = _.county + ibis.literal('-') + _.state_id)
            .select('key', 'geometry')
            .right_join(vote_county, "key")
            .drop('key_right')
            .mutate(jurisdiction = ibis.literal("County"))
            .cast({"geometry": "geometry"})
             )


In [ ]:
vote_local = (votes
                .filter(_["Jurisdiction Type"] == "Municipal")
                .rename(city = "Jurisdiction Name", state_id = "State")
                .mutate(key = _.city + ibis.literal('-') + _.state_id)
                .rename(amount = 'Conservation Funds at Stake', yes = '% Yes')
                .mutate(amount_n=_.amount.replace('$', '').replace(',', '').cast('float'))
                .mutate(log_amount=_.amount_n.log())
                .mutate(year=_['Date'].year().cast('int32'))
                .mutate(
                    yes=ibis.case()
                        .when(_.yes.isin(['Pass', 'None','Fail']), None)  # Handle non-numeric cases
                        .when(_.yes.notnull(), (_.yes.replace('%', '').cast('float').round(2).cast(dt.float64)).cast(dt.string) + '%')  # Convert valid percentages and add %
                        .else_(None)  # Default to None for other cases
                        .end()
                )
              .mutate(log_amount = _.log_amount.round(4))
                .select('key', 'Status', 'yes', 'year', 'amount', 'log_amount', )
                )

df_local = (locality
            .mutate(key = _.name + ibis.literal('-') + _.state_id)
            .select('key', 'geometry')
            .right_join(vote_local, "key")
            .drop('key_right')
            .mutate(jurisdiction = ibis.literal("Municipal"))
            .cast({"geometry": "geometry"})
            .mutate(geometry = _.geometry.buffer(.07))
            )


In [ ]:
df = df_county.union(df_local)

In [ ]:
import subprocess
import os
from huggingface_hub import HfApi, login
import streamlit as st

login(st.secrets["HF_TOKEN"])
# api = HfApi(add_to_git_credential=False)
api = HfApi()

def hf_upload(file, repo_id):
    info = api.upload_file(
            path_or_fileobj=file,
            path_in_repo=file,
            repo_id=repo_id,
            repo_type="dataset",
        )
def generate_pmtiles(input_file, output_file, max_zoom=12):
    # Ensure Tippecanoe is installed
    if subprocess.call(["which", "tippecanoe"], stdout=subprocess.DEVNULL) != 0:
        raise RuntimeError("Tippecanoe is not installed or not in PATH")

    # Construct the Tippecanoe command
    command = [
        "tippecanoe",
        "-o", output_file,
        "-zg",
        "--extend-zooms-if-still-dropping",
        "--force",
        "--projection", "EPSG:4326",  
        input_file
    ]

    # Run Tippecanoe
    try:
        subprocess.run(command, check=True)
        print(f"Successfully generated PMTiles file: {output_file}")
    except subprocess.CalledProcessError as e:
        print(f"Error running Tippecanoe: {e}")



In [ ]:
gdf= df.execute()
gdf = gdf.set_crs("EPSG:4326")

gdf.to_file("vote.geojson")
hf_upload("vote.geojson", "boettiger-lab/landvote")

generate_pmtiles("vote.geojson", "vote.pmtiles")
hf_upload("vote.pmtiles", "boettiger-lab/landvote")



gdf_states= df_states.execute()
gdf_states = gdf_states.set_crs("EPSG:4326")

gdf_states.to_file("vote_states.geojson")
hf_upload("vote_states.geojson", "boettiger-lab/landvote")

generate_pmtiles("vote_states.geojson", "vote_states.pmtiles")
hf_upload("vote_states.pmtiles", "boettiger-lab/landvote")



In [ ]:
import leafmap.maplibregl as leafmap
m = leafmap.Map(style="positron")


url_states = "https://huggingface.co/datasets/boettiger-lab/landvote/resolve/main/vote_states.pmtiles"

outcome = [
      'match',
      ['get', 'Status'], 
      "Pass", '#2E865F',
      "Fail", '#FF3300', 
      '#ccc'
    ]
paint_states = {"fill-color": outcome, 
         # "fill-opacity": 0.2,
        }
style_states = {
    "layers": [
        {
            "id": "votes_states",
            "source": "vote_states",
            "source-layer": "vote_states",
            "type": "fill",
            "filter": [
                "==",
                ["get", "year"],
                2022,
            ],  # only show buildings with height info
            "paint": paint_states
        },
    ],
}

m.add_pmtiles(
    url_states,
    style=style_states,
    visible=True,
    opacity=0.4,
    tooltip=True,
    fit_bounds=False,
)

m

